In [3]:
import pandas as pd
import geopandas as gpd
import matplotlib.pyplot as plt
import numpy as np
from pyproj import CRS
import pathlib
from pathlib import Path
from shapely import wkt
from tqdm import tqdm

import math
import codecs
import osm2geojson
from shapely import wkt

import gzip
from xml.etree.ElementTree import Element, SubElement, Comment, tostring
import xml.etree.ElementTree as ET

import os

# set the working directory
BASE_DIR = Path.cwd()
# define the exported folder path
# Check if folder exists
folder_path = pathlib.Path(BASE_DIR.parent.joinpath("Exported_Files","census_tract","agg_network"))
folder_path.mkdir(parents=True, exist_ok=True)
# print(BASE_DIR)

In [12]:
gdSFdb = pd.read_csv(BASE_DIR.parent.joinpath(folder_path,"Feb122022","SF_merged.csv"))

gdSFdb.drop(columns=["Unnamed: 0"],inplace=True)

gdSFdb2010 = gdSFdb[gdSFdb["ACCIDENT_YEAR"]==2010].add_suffix("_2010").copy()
gdSFdb2016 = gdSFdb[gdSFdb["ACCIDENT_YEAR"]==2016].add_suffix("_2016").copy()
dfSFJoined = pd.merge(gdSFdb2010,gdSFdb2016, left_on="tractce10_2010",right_on="tractce10_2016")
dfSFJoined.rename(columns={"tractce10_2010":"tractce"},inplace=True)
dfSFJoined = dfSFJoined.sort_index(axis=1)
dfSFJoined.to_csv(BASE_DIR.parent.joinpath(folder_path,"Feb122022","SF_joined.csv"))

def add_column(df):
        cols = ['TIME', 'BUSVOL_AM', 'BUSVOL_MD', 'BUSVOL_PM', 'BUSVOL_EV', 'BUSVOL_EA', 'V_1', 'TIME_1', 'CSPD_1', 'V1_1', 'V2_1', 'V3_1', 'V4_1', 'V5_1', 'V6_1', 'V7_1', 'V8_1', 'V9_1', 'V10_1', 'V11_1', 'V12_1', 'VT_1', 'V1T_1', 'V2T_1', 'V3T_1', 'V4T_1', 'V5T_1', 'V6T_1', 'V7T_1', 'V8T_1', 'V9T_1', 'V10T_1', 'V11T_1', 'V12T_1', 'Tot_CAP', 'OOS', 'PUDO', 'Tot_Vol', 'TNC_Tot_Vol', 'Length_meters', 'V13_1', 'V14_1', 'V15_1', 'V16_1', 'V17_1', 'V18_1', 'V19_1', 'V13T_1', 'V14T_1', 'V15T_1', 'V16T_1', 'V17T_1', 'V18T_1', 'V19T_1', 'NUMBER_KILLED', 'NUMBER_INJURED', 'COUNT_SEVERE_INJ', 'COUNT_VISIBLE_INJ', 'COUNT_COMPLAINT_PAIN', 'COUNT_PED_KILLED', 'COUNT_PED_INJURED', 'COUNT_BICYCLIST_KILLED', 'COUNT_BICYCLIST_INJURED', 'COUNT_MC_KILLED', 'COUNT_MC_INJURED', 'Total_Crash', 'COUNT_Fatal', 'COUNT_Severe_Injury', 'COUNT_Visible_Injury', 'COUNT_Other_Injury', 'COUNT_PDO', 'Tot_Vol_yr', 'PUDO_yr', 'OOS_yr', 'TNC_Tot_Vol_yr', 'Non_TNC_Tot_Vol', 'Non_TNC_Tot_Vol_yr', 'VMT_TNC', 'VMT_Non_TNC', 'VMT_TNC_yr', 'VMT_Non_TNC_yr', 'CONGESTED_SPEED', 'CONGESTED_SPEED_yr', 'PCT_TNC_VOL', 'PCT_TNC_PUDO', 'PCT_PUDO_Tot_Vol', 'PCT_PUDO_TNC_Vol', 'PCT_TNC_VOL_yr', 'PCT_TNC_PUDO_yr', 'PCT_PUDO_Tot_Vol_yr', 'PCT_PUDO_TNC_Vol_yr', 'PUDO_thousands', 'PUDO_millions', 'log_PUDO_thousands', 'log_PUDO_millions', 'PUDO_thousands_yr', 'log_PUDO_thousands_yr', 'PUDO_millions_yr', 'log_PUDO_millions_yr', 'VMT_TNC_mil', 'VMT_Non_TNC_mil', 'log_VMT_TNC_mil', 'log_VMT_Non_TNC_mil', 'VMT_TNC_mil_yr', 'log_VMT_TNC_mil_yr', 'VMT_Non_TNC_mil_yr', 'log_VMT_Non_TNC_mil_yr']
        d = {}
        for col in cols:
                d[f'{col}_{"diff"}'] = df[f'{col}_{"2016"}'] - df[f'{col}_{"2010"}']
                d[f'{col}_{"pct_change"}'] = d[f'{col}_{"diff"}'].divide(df[f'{col}_{"2010"}'])
        return pd.concat([df, pd.DataFrame(d, index=df.index)],axis=1)
dfSFJoined = add_column(dfSFJoined)
dfSFJoined.replace([np.inf, -np.inf], np.nan, inplace=True)
dfSFJoined.sort_index(axis=1).to_csv(BASE_DIR.parent.joinpath(folder_path,"Feb122022","SF_joined_diff_pct_chnge.csv"))

gpdSFCT = gpd.read_file(BASE_DIR.parent.joinpath(folder_path,"Feb122022","SF_CT_WGS1984.geojson"), crs = "EPSG:4326")
gpdSFCT = gpdSFCT.merge(dfSFJoined,left_on="tractce10",right_on="tractce",how="left")
# Five times of crashes: 'COUNT_Fatal', 'COUNT_Severe_Injury', 'COUNT_Visible_Injury', 'COUNT_Other_Injury', "COUNT_PDO"
gpdSFCT["COUNT_Fatal_and_Injury_2010"] = gpdSFCT["COUNT_Fatal_2010"] + gpdSFCT["COUNT_Visible_Injury_2010"] + gpdSFCT["COUNT_Severe_Injury_2010"]+ gpdSFCT["COUNT_Other_Injury_2010"]
gpdSFCT["COUNT_Fatal_and_Injury_2016"] = gpdSFCT["COUNT_Fatal_2016"] + gpdSFCT["COUNT_Visible_Injury_2016"] + gpdSFCT["COUNT_Severe_Injury_2016"]+ gpdSFCT["COUNT_Other_Injury_2016"]
gpdSFCT["COUNT_Fatal_and_Injury_diff"] = gpdSFCT["COUNT_Fatal_and_Injury_2016"] - gpdSFCT["COUNT_Fatal_and_Injury_2010"]
gpdSFCT["COUNT_Fatal_and_Injury_pct_change"] = gpdSFCT["COUNT_Fatal_and_Injury_diff"].divide(gpdSFCT["COUNT_Fatal_and_Injury_2010"])

gpdSFCT.to_file(BASE_DIR.parent.joinpath(folder_path, "Feb122022", "SF_CensusTract_refactored_diff_pct_change_WGS1984.geojson"),crs="EPSG:4326")
dfSFCT = gpdSFCT.drop(columns=["geometry"])
dfSFCT.sort_index(axis=1).to_csv(BASE_DIR.parent.joinpath(folder_path, "Feb122022", "SF_CensusTract_refactored_diff_pct_change_WGS1984.csv"))

gpdSFCT= gpd.read_file(BASE_DIR.parent.joinpath(folder_path, "Feb122022", "SF_CensusTract_refactored_diff_pct_change_WGS1984.geojson"),crs="EPSG:4326")
dfSFCT.fillna(0,inplace=True)

input_variable = "Total_Crash"
gpdSFCT[f"{input_variable}_pct_change"]=gpdSFCT[f"{input_variable}_pct_change"]*100

c:\users\goyal\.virtualenvs\overpass_turbo-zwxzihl_\lib\site-packages\geopandas\io\file.py:362: FutureWarning: pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.
  pd.Int64Index,


In [ ]:
print(gpdSFCT.columns.to_list())

In [16]:
# diversify color range using styling function

import branca

# colormap = branca.colormap.LinearColormap(
#         vmin=min(gpdSFCT[f"{input_variable}_pct_change"]),
#         vmax=max(gpdSFCT[f"{input_variable}_pct_change"]),
#         colors=[ "darkgreen","green","lightblue", "orange","red",],
#         caption=f" {input_variable} (%) change",
# ).to_step(n=12)

linear_color_red = branca.colormap.LinearColormap(["#ffb2b2","#ff7f7f","#ff4c4c","#ff1919"],
                                     vmin=np.nanmin(gpdSFCT.loc[gpdSFCT[f"{input_variable}_pct_change"]>=0,f"{input_variable}_pct_change"]),
                                     vmax=np.nanmax(gpdSFCT.loc[gpdSFCT[f"{input_variable}_pct_change"]>=0,f"{input_variable}_pct_change"]), caption ="% difference").to_step(10)

linear_color_green = branca.colormap.LinearColormap(["#008000","#329932","#66b266","#99cc99"],
                                       vmin=np.nanmin(gpdSFCT.loc[gpdSFCT[f"{input_variable}_pct_change"]<0,f"{input_variable}_pct_change"]),
                                       vmax=np.nanmax(gpdSFCT.loc[gpdSFCT[f"{input_variable}_pct_change"]<0,f"{input_variable}_pct_change"])).to_step(10)

def get_linear_color(feature_attribute):
        if feature_attribute>0:
                return linear_color_red(feature_attribute)
        elif feature_attribute<0:
                return linear_color_green(feature_attribute)
        else:
                return "#ffffff"

import folium
from folium.features import GeoJsonPopup, GeoJsonTooltip
SFMap = folium.Map(location=[37.76002622191773, -122.44313142442648], zoom_start=11)


popup = GeoJsonPopup(
        fields=["tractce10", f"{input_variable}_2010", f"{input_variable}_2016",f"{input_variable}_diff",f"{input_variable}_pct_change" ],
        aliases=["State", "YR2010" ,"YR2016", "Diff (YR2016-YR2010)", "% Change"],
        localize=True,
        labels=True,
        style="background-color: yellow;",
)

tooltip = GeoJsonTooltip(
        fields=["tractce10", f"{input_variable}_2010", f"{input_variable}_2016",f"{input_variable}_diff",f"{input_variable}_pct_change" ],
        aliases=["State", "YR2010" ,"YR2016", "Diff (YR2016-YR2010)", "% Change"],
        localize=True,
        sticky=False,
        labels=True,
        style="""
        background-color: #F0EFEF;
        border: 2px solid black;
        border-radius: 3px;
                box-shadow: 3px;
    """,
        max_width=800,
)

# g = folium.GeoJson(
#         gpdSFCT,
#         style_function=lambda x: {
#                 "fillColor": colormap(x["properties"][f"{input_variable}_pct_change"])
#                 if x["properties"][f"{input_variable}_pct_change"] is not None
#                 else "transparent",
#                 "color": "black",
#                 "fillOpacity": 0.4,
#         },
#         tooltip=tooltip,
#         popup=popup,
# ).add_to(SFMap)

g = folium.GeoJson(
        gpdSFCT,
        style_function=lambda x: {
                "fillColor": get_linear_color(x["properties"][f"{input_variable}_pct_change"])
                if x["properties"][f"{input_variable}_pct_change"] is not None
                else "transparent",
                "color": "black",
                "fillOpacity": 0.85,
        },
        tooltip=tooltip,
        popup=popup,
).add_to(SFMap)

folium.LayerControl().add_to(SFMap)

outfp = BASE_DIR.parent.joinpath(folder_path, "Feb122022", f"SF_CensusTract_{input_variable}_map.geojson")
SFMap.save(outfp)

SFMap

In [38]:

# # folium map
# import folium
# SFMap = folium.Map(location=[37.76002622191773, -122.44313142442648], zoom_start=11)
#

#
# choropleth = folium.Choropleth(
#         geo_data=gpdSFCT,
#         data = dfSFCT,
#         name="choropleth",
#         columns=["tractce10",f"{input_variable}_pct_change"],
#         key_on="feature.properties.tractce10",
#         fill_color="YlOrRd",
#         fill_opacity=0.7,
#         line_opacity=0.2,
#         legend_name=f"{input_variable} (%) change",
# ).add_to(SFMap)
#
# from folium.features import GeoJsonPopup, GeoJsonTooltip
# # GeoJsonPopup().add_to(choropleth.geojson)
# # geo_json = folium.GeoJson(nodeData, popup=folium.GeoJsonPopup(fields=['name']))
#
# # creating a indexed version of the dataframe so we can lookup values
# dfSFCT_indexed = dfSFCT.set_index('tractce10')
#
# # looping thru the geojson object and adding a each census tract and corresponding value
# # and assigning a value from our dataframe
# for s in choropleth.geojson.data['features']:
#         txt = s['properties']['tractce']
#         s['properties']['Total_Crash_pct_change'] = dfSFCT_indexed.loc[s['properties']['tractce10'], 'Total_Crash_pct_change']
#
# # and finally adding a tooltip/hover to the choropleth's geojson
# folium.GeoJsonTooltip(['tractce10', f"{input_variable}_2010", f"{input_variable}_2016",f"{input_variable}_diff",f"{input_variable}_pct_change" ]).add_to(choropleth.geojson)
#
# folium.LayerControl().add_to(SFMap)
#
# SFMap